# Imports

In [61]:
import numpy as np
import pandas as pd
import math
import matplotlib.pyplot as plt

from tensorflow.keras.layers import Activation, Dense, Input, Conv2D, Flatten, Reshape, Conv2DTranspose, LeakyReLU, BatchNormalization
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras.models import Model
from tensorflow.keras.datasets import mnist
from tensorflow.keras.utils import to_categorical, plot_model

import os

# Data load and Preprocessing

In [17]:
(x_train, _), (_, _) = mnist.load_data()

In [18]:
image_size = x_train.shape[1]
x_train = np.reshape(x_train, [-1, image_size, image_size, 1])
x_train = x_train.astype('float32') / 255

# Hyperparameter

In [19]:
latent_size = 100
batch_size = 64
train_steps = 40000
lr = 2e-4
decay = 6e-8
input_shape = (image_size, image_size, 1)

# Generator

In [28]:
input_shape_gen = (latent_size, )
kernel_size = 5
image_resize = image_size // 4

In [29]:
inputs_g = Input(shape = input_shape_gen, name = 'z_input')
x = Dense(image_resize * image_resize * layer_filters[0])(inputs_g)
x = Reshape((image_resize, image_resize, layer_filters[0]))(x)

x = BatchNormalization()(x)
x = Activation('relu')(x)
x = Conv2DTranspose(filters = 128, kernel_size = kernel_size, strides=2, padding='same')(x)

x = BatchNormalization()(x)
x = Activation('relu')(x)
x = Conv2DTranspose(filters = 64, kernel_size = kernel_size, strides= 2, padding='same')(x)

x = BatchNormalization()(x)
x = Activation('relu')(x)
x = Conv2DTranspose(filters = 32, kernel_size = kernel_size, strides=1, padding='same')(x)

x = BatchNormalization()(x)
x = Activation('relu')(x)
x = Conv2DTranspose(filters = 1, kernel_size = kernel_size, strides=1, padding='same')(x)
x = Activation('sigmoid')(x)

In [30]:
gen = Model(inputs_g, x, name='generator')

In [31]:
gen.summary()

Model: "generator"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
z_input (InputLayer)         [(None, 100)]             0         
_________________________________________________________________
dense_3 (Dense)              (None, 6272)              633472    
_________________________________________________________________
reshape_2 (Reshape)          (None, 7, 7, 128)         0         
_________________________________________________________________
batch_normalization_8 (Batch (None, 7, 7, 128)         512       
_________________________________________________________________
activation_10 (Activation)   (None, 7, 7, 128)         0         
_________________________________________________________________
conv2d_transpose_8 (Conv2DTr (None, 14, 14, 128)       409728    
_________________________________________________________________
batch_normalization_9 (Batch (None, 14, 14, 128)       51

# Discriminator

In [40]:
inputs_d = Input(shape = input_shape, name = 'discriminatr_input')
d = LeakyReLU(alpha=0.2)(inputs_d)
d = Conv2D(filters = 32, kernel_size = kernel_size, strides = 2, padding='same')(d)

d = LeakyReLU(alpha=0.2)(d)
d = Conv2D(filters = 64, kernel_size = kernel_size, strides = 2, padding='same')(d)

d = LeakyReLU(alpha=0.2)(d)
d = Conv2D(filters = 128, kernel_size = kernel_size, strides = 2, padding='same')(d)

d = LeakyReLU(alpha=0.2)(d)
d = Conv2D(filters = 256, kernel_size = kernel_size, strides = 1, padding='same')(d)

d = Flatten()(d)
d = Dense(1)(d)
d = Activation('sigmoid')(d)

In [41]:
dis = Model(inputs_d, d, name='discriminator')

In [42]:
dis.summary()

Model: "discriminator"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
discriminatr_input (InputLay [(None, 28, 28, 1)]       0         
_________________________________________________________________
leaky_re_lu_16 (LeakyReLU)   (None, 28, 28, 1)         0         
_________________________________________________________________
conv2d_16 (Conv2D)           (None, 14, 14, 32)        832       
_________________________________________________________________
leaky_re_lu_17 (LeakyReLU)   (None, 14, 14, 32)        0         
_________________________________________________________________
conv2d_17 (Conv2D)           (None, 7, 7, 64)          51264     
_________________________________________________________________
leaky_re_lu_18 (LeakyReLU)   (None, 7, 7, 64)          0         
_________________________________________________________________
conv2d_18 (Conv2D)           (None, 4, 4, 128)       

In [43]:
optimizer = RMSprop(lr = lr, decay = decay)

In [44]:
dis.compile(loss='binary_crossentropy', optimizer = optimizer, metrics=['accuracy'])

# Model

In [45]:
optimizer_m = RMSprop(lr=lr*0.5, decay=decay*0.5)

In [46]:
dis.trainable = False

In [48]:
adv = Model(inputs, dis(gen(inputs)), name='GAN')

In [50]:
adv.compile(loss='binary_crossentropy', optimizer=optimizer_m, metrics=['accuracy'])

In [51]:
adv.summary()

Model: "GAN"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
z_input (InputLayer)         [(None, 100)]             0         
_________________________________________________________________
generator (Functional)       (None, 28, 28, 1)         1301505   
_________________________________________________________________
discriminator (Functional)   (None, 1)                 1080577   
Total params: 2,382,082
Trainable params: 1,300,801
Non-trainable params: 1,081,281
_________________________________________________________________


# Train

In [98]:
def train(models, x_train, params):
    generator, discriminator, adversarial = models
    batch_size, latent_size, train_steps = params
    save_interval = 500
    noise_input = np.random.uniform(-1.0, 1.0, size=[16, latent_size])
    train_size = x_train.shape[0]
    for i in range(train_steps):
        rand_indexes = np.random.randint(0, train_size, size=batch_size)
        real_images = x_train[rand_indexes]
        noise = np.random.uniform(-1.0,
                                  1.0,
                                  size=[batch_size, latent_size])
        fake_images = generator.predict(noise)
        x = np.concatenate((real_images, fake_images))
        y = np.ones([2 * batch_size, 1])
        y[batch_size:, :] = 0.0
        loss, acc = discriminator.train_on_batch(x, y)
        log = "%d: [discriminator loss: %f, acc: %f]" % (i, loss, acc)

        noise = np.random.uniform(-1.0,
                                  1.0, 
                                  size=[batch_size, latent_size])

        y = np.ones([batch_size, 1])

        loss, acc = adversarial.train_on_batch(noise, y)
        log = "%s [adversarial loss: %f, acc: %f]" % (log, loss, acc)
        print(log)


In [62]:
models = (gen, dis, adv)
params = (batch_size, latent_size, train_steps)
train(models, x_train, params)

0: [discriminator loss: 0.485398, acc: 0.765625] [adversarial loss: 0.001233, acc: 1.000000]
1: [discriminator loss: 2.235703, acc: 0.500000] [adversarial loss: 7.216573, acc: 0.000000]
2: [discriminator loss: 0.395185, acc: 0.804688] [adversarial loss: 1.436291, acc: 0.000000]
3: [discriminator loss: 0.186287, acc: 0.984375] [adversarial loss: 3.023690, acc: 0.000000]
4: [discriminator loss: 0.130950, acc: 1.000000] [adversarial loss: 3.342116, acc: 0.000000]
5: [discriminator loss: 0.350395, acc: 0.929688] [adversarial loss: 3.503277, acc: 0.000000]
6: [discriminator loss: 0.476827, acc: 0.796875] [adversarial loss: 0.051542, acc: 1.000000]
7: [discriminator loss: 0.802747, acc: 0.539062] [adversarial loss: 6.740178, acc: 0.000000]
8: [discriminator loss: 1.284458, acc: 0.570312] [adversarial loss: 0.013191, acc: 1.000000]
9: [discriminator loss: 1.055611, acc: 0.546875] [adversarial loss: 3.262222, acc: 0.000000]
10: [discriminator loss: 0.272484, acc: 0.906250] [adversarial loss: 0

91: [discriminator loss: 0.016037, acc: 1.000000] [adversarial loss: 0.042927, acc: 1.000000]
92: [discriminator loss: 0.028937, acc: 1.000000] [adversarial loss: 0.076859, acc: 1.000000]
93: [discriminator loss: 0.039245, acc: 0.992188] [adversarial loss: 0.076247, acc: 1.000000]
94: [discriminator loss: 0.028219, acc: 0.992188] [adversarial loss: 0.116495, acc: 1.000000]
95: [discriminator loss: 0.020895, acc: 1.000000] [adversarial loss: 0.056877, acc: 1.000000]
96: [discriminator loss: 0.024737, acc: 1.000000] [adversarial loss: 0.080497, acc: 1.000000]
97: [discriminator loss: 0.023787, acc: 1.000000] [adversarial loss: 0.068760, acc: 1.000000]
98: [discriminator loss: 0.016609, acc: 1.000000] [adversarial loss: 0.115666, acc: 1.000000]
99: [discriminator loss: 0.011099, acc: 1.000000] [adversarial loss: 0.180278, acc: 0.984375]
100: [discriminator loss: 0.017965, acc: 1.000000] [adversarial loss: 0.102189, acc: 1.000000]
101: [discriminator loss: 0.010015, acc: 1.000000] [adversa

181: [discriminator loss: 0.002987, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
182: [discriminator loss: 0.000188, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
183: [discriminator loss: 0.000165, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
184: [discriminator loss: 0.000254, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
185: [discriminator loss: 0.000355, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
186: [discriminator loss: 0.000447, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
187: [discriminator loss: 0.000162, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
188: [discriminator loss: 0.000200, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
189: [discriminator loss: 0.000180, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
190: [discriminator loss: 0.000214, acc: 1.000000] [adversarial loss: 0.000000, acc: 1.000000]
191: [discriminator loss: 0.000216, acc: 1.000000]

270: [discriminator loss: 0.074825, acc: 0.984375] [adversarial loss: 0.027611, acc: 1.000000]
271: [discriminator loss: 0.033022, acc: 0.992188] [adversarial loss: 0.006755, acc: 1.000000]
272: [discriminator loss: 0.063755, acc: 0.960938] [adversarial loss: 0.006938, acc: 1.000000]
273: [discriminator loss: 0.040610, acc: 0.976562] [adversarial loss: 0.006970, acc: 1.000000]
274: [discriminator loss: 0.051421, acc: 0.976562] [adversarial loss: 0.008174, acc: 1.000000]
275: [discriminator loss: 0.051258, acc: 0.976562] [adversarial loss: 0.054424, acc: 1.000000]
276: [discriminator loss: 0.025581, acc: 1.000000] [adversarial loss: 0.125140, acc: 0.968750]
277: [discriminator loss: 0.089760, acc: 0.960938] [adversarial loss: 0.016519, acc: 1.000000]
278: [discriminator loss: 0.210420, acc: 0.921875] [adversarial loss: 1.205199, acc: 0.390625]
279: [discriminator loss: 0.170761, acc: 0.921875] [adversarial loss: 0.000032, acc: 1.000000]
280: [discriminator loss: 0.022296, acc: 0.984375]

359: [discriminator loss: 0.089539, acc: 0.976562] [adversarial loss: 0.062402, acc: 1.000000]
360: [discriminator loss: 0.198494, acc: 0.914062] [adversarial loss: 0.514049, acc: 0.734375]
361: [discriminator loss: 0.196186, acc: 0.906250] [adversarial loss: 0.004933, acc: 1.000000]
362: [discriminator loss: 0.263700, acc: 0.890625] [adversarial loss: 1.335687, acc: 0.296875]
363: [discriminator loss: 0.318412, acc: 0.867188] [adversarial loss: 0.004640, acc: 1.000000]
364: [discriminator loss: 0.746825, acc: 0.718750] [adversarial loss: 4.478461, acc: 0.015625]
365: [discriminator loss: 0.992690, acc: 0.585938] [adversarial loss: 0.013848, acc: 1.000000]
366: [discriminator loss: 0.025055, acc: 1.000000] [adversarial loss: 0.006358, acc: 1.000000]
367: [discriminator loss: 0.020774, acc: 1.000000] [adversarial loss: 0.004628, acc: 1.000000]
368: [discriminator loss: 0.027291, acc: 1.000000] [adversarial loss: 0.003621, acc: 1.000000]
369: [discriminator loss: 0.039484, acc: 0.976562]

...

39612: [discriminator loss: 0.475370, acc: 0.765625] [adversarial loss: 1.110511, acc: 0.281250]
39613: [discriminator loss: 0.516978, acc: 0.750000] [adversarial loss: 1.272638, acc: 0.156250]
39614: [discriminator loss: 0.496927, acc: 0.750000] [adversarial loss: 1.154981, acc: 0.281250]
39615: [discriminator loss: 0.456468, acc: 0.757812] [adversarial loss: 1.199215, acc: 0.312500]
39616: [discriminator loss: 0.482976, acc: 0.757812] [adversarial loss: 1.128963, acc: 0.406250]
39617: [discriminator loss: 0.507889, acc: 0.734375] [adversarial loss: 1.639548, acc: 0.109375]
39618: [discriminator loss: 0.564863, acc: 0.710938] [adversarial loss: 1.004665, acc: 0.296875]
39619: [discriminator loss: 0.523342, acc: 0.695312] [adversarial loss: 1.536593, acc: 0.171875]
39620: [discriminator loss: 0.551352, acc: 0.695312] [adversarial loss: 1.298745, acc: 0.296875]
39621: [discriminator loss: 0.487954, acc: 0.757812] [adversarial loss: 1.256480, acc: 0.343750]
39622: [discriminator loss: 0.

39700: [discriminator loss: 0.625848, acc: 0.679688] [adversarial loss: 1.917520, acc: 0.093750]
39701: [discriminator loss: 0.591391, acc: 0.687500] [adversarial loss: 0.885706, acc: 0.531250]
39702: [discriminator loss: 0.490684, acc: 0.773438] [adversarial loss: 1.427290, acc: 0.171875]
39703: [discriminator loss: 0.555674, acc: 0.726562] [adversarial loss: 1.294680, acc: 0.203125]
39704: [discriminator loss: 0.485227, acc: 0.781250] [adversarial loss: 1.093551, acc: 0.390625]
39705: [discriminator loss: 0.548323, acc: 0.695312] [adversarial loss: 1.571070, acc: 0.093750]
39706: [discriminator loss: 0.521612, acc: 0.742188] [adversarial loss: 1.009217, acc: 0.265625]
39707: [discriminator loss: 0.500933, acc: 0.757812] [adversarial loss: 1.497919, acc: 0.125000]
39708: [discriminator loss: 0.464970, acc: 0.765625] [adversarial loss: 1.408888, acc: 0.156250]
39709: [discriminator loss: 0.480427, acc: 0.718750] [adversarial loss: 1.191894, acc: 0.312500]
39710: [discriminator loss: 0.

39788: [discriminator loss: 0.447770, acc: 0.765625] [adversarial loss: 1.455800, acc: 0.203125]
39789: [discriminator loss: 0.423303, acc: 0.781250] [adversarial loss: 1.493285, acc: 0.218750]
39790: [discriminator loss: 0.561139, acc: 0.632812] [adversarial loss: 1.295818, acc: 0.250000]
39791: [discriminator loss: 0.524003, acc: 0.742188] [adversarial loss: 1.631134, acc: 0.109375]
39792: [discriminator loss: 0.526156, acc: 0.742188] [adversarial loss: 1.207339, acc: 0.234375]
39793: [discriminator loss: 0.568740, acc: 0.687500] [adversarial loss: 1.462862, acc: 0.171875]
39794: [discriminator loss: 0.507957, acc: 0.789062] [adversarial loss: 1.116922, acc: 0.343750]
39795: [discriminator loss: 0.571595, acc: 0.710938] [adversarial loss: 1.324167, acc: 0.234375]
39796: [discriminator loss: 0.550861, acc: 0.718750] [adversarial loss: 1.166935, acc: 0.265625]
39797: [discriminator loss: 0.519404, acc: 0.757812] [adversarial loss: 1.452838, acc: 0.125000]
39798: [discriminator loss: 0.

39875: [discriminator loss: 0.555424, acc: 0.687500] [adversarial loss: 1.003400, acc: 0.328125]
39876: [discriminator loss: 0.590498, acc: 0.679688] [adversarial loss: 1.217637, acc: 0.390625]
39877: [discriminator loss: 0.529152, acc: 0.703125] [adversarial loss: 1.276081, acc: 0.234375]
39878: [discriminator loss: 0.485581, acc: 0.757812] [adversarial loss: 1.193128, acc: 0.281250]
39879: [discriminator loss: 0.533320, acc: 0.703125] [adversarial loss: 1.327284, acc: 0.250000]
39880: [discriminator loss: 0.579315, acc: 0.734375] [adversarial loss: 1.026564, acc: 0.343750]
39881: [discriminator loss: 0.525351, acc: 0.757812] [adversarial loss: 1.376275, acc: 0.062500]
39882: [discriminator loss: 0.533977, acc: 0.703125] [adversarial loss: 1.134130, acc: 0.281250]
39883: [discriminator loss: 0.550429, acc: 0.718750] [adversarial loss: 1.764414, acc: 0.062500]
39884: [discriminator loss: 0.572040, acc: 0.656250] [adversarial loss: 0.996685, acc: 0.484375]
39885: [discriminator loss: 0.

39963: [discriminator loss: 0.506988, acc: 0.750000] [adversarial loss: 1.361539, acc: 0.265625]
39964: [discriminator loss: 0.651045, acc: 0.648438] [adversarial loss: 1.600626, acc: 0.187500]
39965: [discriminator loss: 0.521460, acc: 0.695312] [adversarial loss: 1.035756, acc: 0.390625]
39966: [discriminator loss: 0.598251, acc: 0.710938] [adversarial loss: 1.484122, acc: 0.250000]
39967: [discriminator loss: 0.471763, acc: 0.750000] [adversarial loss: 1.119493, acc: 0.265625]
39968: [discriminator loss: 0.480733, acc: 0.742188] [adversarial loss: 1.162158, acc: 0.281250]
39969: [discriminator loss: 0.571534, acc: 0.718750] [adversarial loss: 1.368282, acc: 0.203125]
39970: [discriminator loss: 0.601739, acc: 0.640625] [adversarial loss: 1.325680, acc: 0.218750]
39971: [discriminator loss: 0.524089, acc: 0.718750] [adversarial loss: 1.240812, acc: 0.281250]
39972: [discriminator loss: 0.597181, acc: 0.687500] [adversarial loss: 1.308787, acc: 0.203125]
39973: [discriminator loss: 0.

In [97]:
gen.save('generator.h5')